<a href="https://colab.research.google.com/github/jalkestrup/dtu-deep-project/blob/main/llm2vec_scandeval_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Setting up colab env

In [2]:
! pip install -q seb
! pip install -q llm2vec
! pip install -q -U "huggingface_hub[cli]"

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.7/83.7 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.0/44.0 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.6/53.6 kB 4.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 702.3/702.3 kB 21.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.2/119.2 kB 6.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.1/542.1 kB 25.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 172.0/172.0 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 219.2/219.2 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [5]:
! huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) n
Token is valid (permission: write).
The token `lighting-ai` has been saved to /root/.cache/huggingface/stored_tokens
Your token has been saved to /root/.cache/huggingface/token
Login successful.
The current active token is: `lighting-ai`

## Loading LLM model

In [6]:
from llm2vec import LLM2Vec

import torch
from transformers import AutoTokenizer, AutoModel, AutoConfig
from peft import PeftModel

# Loading base Mistral model, along with custom code that enables bidirectional connections in decoder-only LLMs. MNTP LoRA weights are merged into the base model.
tokenizer = AutoTokenizer.from_pretrained(
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp"
)
config = AutoConfig.from_pretrained(
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp", trust_remote_code=True
)
model = AutoModel.from_pretrained(
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp",
    trust_remote_code=True,
    config=config,
    torch_dtype=torch.bfloat16,
    device_map="cuda" if torch.cuda.is_available() else "cpu",
)
model = PeftModel.from_pretrained(
    model,
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp",
)
model = model.merge_and_unload()  # This can take several minutes on cpu

# Loading supervised model. This loads the trained LoRA weights on top of MNTP model. Hence the final weights are -- Base model + MNTP (LoRA) + supervised (LoRA).
model = PeftModel.from_pretrained(
    model, "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp-supervised"
)

# Wrapper for encoding and pooling operations
l2v = LLM2Vec(model, tokenizer, pooling_mode="mean", max_length=512)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:797: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/871 [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/434 [00:00<?, ?B/s]

...

pytorch_model.bin:   0%|          | 0.00/5.38G [00:00<?, ?B/s]

Some weights of the model checkpoint at princeton-nlp/Sheared-LLaMA-1.3B were not used when initializing LlamaEncoderModel: ['lm_head.weight']
- This IS expected if you are initializing LlamaEncoderModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing LlamaEncoderModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


adapter_model.safetensors:   0%|          | 0.00/30.0M [00:00<?, ?B/s]

adapter_config.json:   0%|          | 0.00/791 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/30.0M [00:00<?, ?B/s]

## Set up model in SEB and run eval
Intanstiate a custom model in the scandinavian embedding benchmark

~ Took +2 hrs to run 70% of eval when I interuped

In [7]:
from sentence_transformers import SentenceTransformer
from typing import Any
import seb
import numpy as np


model_name = "LLM2Vec-Sheared-LLaMA-mntp-supervised"


class MyEncoder(seb.Encoder):
    """
    A custom model for SEB that uses the SentenceTransformer library.
    """

    def __init__(self, l2v):
        self.model = l2v

    def encode(  # type: ignore
        self,
        sentences: list[str],
        *,
        task: seb.Task,
        **kwargs: Any,
    ) -> np.ndarray:
        if task.name == "DKHate":  # allow you to embed differently based on the task
            emb = self.model.encode(sentences, batch_size=32)
        else:
            emb = self.model.encode(sentences, batch_size=32)  # here we just do the same for all tasks
        return emb


@seb.models.register(model_name)  # add the model to the registry
def create_my_model() -> seb.SebModel:
    hf_name = model_name

    # create meta data
    meta = seb.ModelMeta(
        name=hf_name.split("/")[-1],
        huggingface_name=hf_name,
        reference="https://huggingface.co/McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp-supervised",
        languages=[],
        embedding_size=4096,
    )
    return seb.SebModel(
        encoder=MyEncoder(l2v),
        meta=meta,
    )

In [ ]:
import seb

models = [seb.get_model("LLM2Vec-Sheared-LLaMA-mntp-supervised")]
# for simplicity, we will only run it with one model, but you could run it with multiple models:
# models = seb.get_all_models()

full_benchmark = seb.Benchmark()
results = full_benchmark.evaluate_models(models=models)

Running LLM2Vec-Sheared-LLaMA-mntp-supervised:   0%|          | 0/24 [00:00<?, ?it/s]
Running LLM2Vec-Sheared-LLaMA-mntp-supervised on Angry Tweets:   0%|          | 0/24 [00:00<?, ?it/s]
Running LLM2Vec-Sheared-LLaMA-mntp-supervised on LCC:   0%|          | 0/24 [00:00<?, ?it/s]         
Running LLM2Vec-Sheared-LLaMA-mntp-supervised on Bornholm Parallel:   0%|          | 0/24 [00:00<?, ?it/s]
Running LLM2Vec-Sheared-LLaMA-mntp-supervised on DKHate:   0%|          | 0/24 [00:00<?, ?it/s]           

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/2960 [00:00<?, ? examples/s]

Map:   0%|          | 0/329 [00:00<?, ? examples/s]

...



Clustering:  75%|███████▌  | 3/4 [06:52<02:17, 137.59s/it]

Batches:   0%|          | 0/16 [00:00<?, ?it/s]



Clustering: 100%|██████████| 4/4 [09:10<00:00, 137.63s/it]

Running LLM2Vec-Sheared-LLaMA-mntp-supervised on SNL Clustering:  71%|███████   | 17/24 [1:30:47<46:56, 402.35s/it]
Running LLM2Vec-Sheared-LLaMA-mntp-supervised on SNL Retrieval:  71%|███████   | 17/24 [1:30:47<46:56, 402.35s/it] 

Batches:   0%|          | 0/41 [00:00<?, ?it/s]

Batches:   0%|          | 0/41 [00:00<?, ?it/s]